In [22]:
import urllib
from bs4 import BeautifulSoup
from pymongo import MongoClient
from datetime import datetime
import calendar
#import scrapy
import re
from bson.objectid import ObjectId









In [23]:
import pymongo
def parseEventPage(month, year):
    #Download the Page Content
    URL = 'https://en.wikipedia.org/wiki/Portal:Current_events/%s_%s' %(month,year)    
    data = urllib.request.urlopen(URL).read()
    soup = BeautifulSoup(data,'html.parser')    

    #Selecting the Title
    body = soup.find('body')
    
    ## define a mongodb client, create a database names WikiEvent
    client = pymongo.MongoClient("localhost", 27017)
    db = client['WikiEvent']
    serverStatusResult=db.command("serverStatus")
    check=body.find_all('tr')[1]
    
    ## extract date for events
    datetables = body.find_all('table', attrs={'class':'plainlinks'})

    ## events on each day identified by td tag with description class attribute
    for date, dailyevent in zip(datetables, body.find_all('td', attrs={'class':'description'})):
        print ('Hi, are you there')
        datenumber = datetime.strptime(re.sub('\s*','',date.find('span', attrs={'class':'bday dtstart published updated'}).text), '%Y-%m-%d')
        datenumber=datenumber.strftime('%b/%d/%Y')
        
        ##categories identified with dt tag
        categories = dailyevent.find_all('dt')
        

         #double equal loop, category and concrete events
        for category,eventcategory in zip(categories,dailyevent.find_all('ul', recursive = False)):
            categorytext = category.text
            
            ## single event identified with li tag. if event has specific event entity page, there will be one more li tag
            for singleevent in eventcategory.find_all('li', recursive=False):
                
                ## event has wikipage
                if singleevent.find('ul'):

                    singles = singleevent.find_all('ul')
                   
                    singleeventsummary = singles.pop().text  ## last li tag, event summary
#                     print(singleeventsummary)
                    ## event title may have multiple subtitles
                    title = [st.get('href') for st in singleevent.find_all('a', recursive=False)]

                    ## subtitle exists
                    if singles:

                        title = title + [single.find('a').get('href') for single in singles]


                    entities = [entitylink.get('href') for entitylink in singleevent.find('ul').find('li').find_all('a') if entitylink.get('title')]
                    external = singleevent.find_all('a', attrs={'class': 'external text'})
                    external_link = [e.get('href') for e in external if external]

                
                else:
                    title = False
                    singleeventsummary = singleevent.text
                    print(singleeventsummary)
                    entities = [entitylink.get('title') for entitylink in singleevent.find_all('a') if entitylink.get('title')]
                    
                    external = singleevent.find_all('a', attrs={'class':'external text'})
                    external_link = [e.get('href') for e in external if external]
                myrecord={"date": datenumber,
                          "category": categorytext,
                          "event_title": title,
                          "event_summary": singleeventsummary,
                          "entities": entities,
			              "person": False,
			              "external_link": external_link
                         }
                print(myrecord)
                db.events_entity_title.insert_one(myrecord)





In [24]:


import urllib.request

In [25]:
import pymongo
def parseEventPage2(month, year):
    #Download the Page Content
    URL = 'https://en.wikipedia.org/wiki/Portal:Current_events/%s_%s' %(month,year)  
    #it sends a GET query to Wikipedia website, then it parses an HTML pagedepending on the received result. 
    #Once it finishes parsing, then the scrapper searches the data in the HTML tags which need to be extracted
    # then it converts it into the specified format
    data = urllib.request.urlopen(URL).read()
    
    # It scrapes the data using two li-braries named Requests and bs4 also known as Beautiful Soup
    soup = BeautifulSoup(data,'html.parser')
    
    #Selecting the Title
    body = soup.find('body')
    
    ## define a mongodb client, create a database names WikiEvent
    client = pymongo.MongoClient("localhost", 27017)

    db = client['WikiEvent']
    serverStatusResult=db.command("serverStatus")
    check=body.find_all('div', attrs={'class':'plainlinks'})[1]
    
    ## extract date for events
    datetables = body.find_all('div', attrs={'class':'plainlinks'})

    ## events on each day identified by td tag with description class attribute
    for date, dailyevent in zip(datetables, body.find_all('div', attrs={'class':'description'})):
        datenumber = datetime.strptime(re.sub('\s*','',date.find('span', attrs={'class':'bday dtstart published updated'}).text), '%Y-%m-%d')
        datenumber=datenumber.strftime('%b/%d/%Y')
        ##categories identified with dt tag
        categories = dailyevent.find_all('div',attrs={'role':'heading'})
        

         #double equal loop, category and concrete events
        for category,eventcategory in zip(categories,dailyevent.find_all('ul', recursive = False)):
            categorytext = category.text
            
            ## single event identified with li tag. if event has specific event entity page, there will be one more li tag
            for singleevent in eventcategory.find_all('li', recursive=False):
                
                ## event has wikipage
                if singleevent.find('ul'):

                    singles = singleevent.find_all('ul')
                   
                    singleeventsummary = singles.pop().text  ## last li tag, event summary

                    ## event title may have multiple subtitles

                    title = [st.get('href') for st in singleevent.find_all('a', recursive=False)]

                    ## subtitle exists
                    if singles:

                        title = title + [single.find('a').get('href') for single in singles]


                    entities = [entitylink.get('href') for entitylink in singleevent.find('ul').find('li').find_all('a') if entitylink.get('title')]
                    external = singleevent.find_all('a', attrs={'class': 'external text'})
                    external_link = [e.get('href') for e in external if external]

#                     print ('event title: ' )
#                     print (title)
                
                else:
                    title = False
                    singleeventsummary = singleevent.text
                    entities = [entitylink.get('title') for entitylink in singleevent.find_all('a') if entitylink.get('title')]
                    
                    external = singleevent.find_all('a', attrs={'class':'external text'})
                    external_link = [e.get('href') for e in external if external]
                    
                myrecord={"date": datenumber,
                          "category": categorytext,
                          "event_title": title,
                          "event_summary": singleeventsummary,
                          "entities": entities,
			              "person": False,
			              "external_link": external_link
                         }
                db.events_entity_title.insert_one(myrecord)
                #document = client.db.collection.find_one({'_id': ObjectId(myrecord)})
                 

In [27]:
if __name__ == '__main__':
#calling functions
    year = ['2016','2017','2018','2019']
    month = [calendar.month_name[i].capitalize()for i in range(1,13)]
    print(month)
    month1= [calendar.month_name[i].capitalize()for i in range(1,5)]
    month2= [calendar.month_name[i].capitalize()for i in range(1,10)]
    
    for y in year:
        if y=='2016':
            for m in month:
                print (y,m)
                parseEventPage(m,y)
        
        elif y=='2017':
                for m in month2:
                    print (y,m)
                    parseEventPage(m,y)
                parseEventPage2('October','2017')
                parseEventPage2('November','2017')
                parseEventPage2('December','2017')
        elif y=='2018':
                for m in month:
                    print (y,m)
                    parseEventPage2(m,y)
                    
        
            
        elif y=='2019':
                for m in month1:
                    print (y,m)
                    parseEventPage2(m,y)
                


['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']
2016 January
Hi, are you there
{'date': 'Jan/01/2016', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/Israeli%E2%80%93Palestinian_conflict'], 'event_summary': "A shooting takes place at a pub in Tel Aviv, Israel, leaving two dead and eight injured. The gunman managed to escape and possibly killed his accomplice, an Arab taxi driver, whose body was found nearby. The police identified the shooter as 30 year old muslim Nisa'at Melkham from Ar'ara and searched his home. (Haaretz)", 'entities': ['/wiki/January_2016_Tel_Aviv_shooting', '/wiki/Tel_Aviv', '/wiki/Israel', '/wiki/Ar%27ara'], 'person': False, 'external_link': ['http://www.haaretz.com/israel-news/1.694926']}
A new 28-foot tall statue of Jesus, dubbed "Jesus de Greatest," is unveiled on New Year's Day outside St. Aloysius Catholic Church in Abajah village, Nigeria's Imo state, which is descri

According to a report in The Japan Times, Major League Baseball is investigating Texas Rangers pitcher Yu Darvish as to whether he had any links with an illegal gambling ring allegedly operated by his brother Sho, who was arrested in October 2015 in Osaka on gambling charges. The ring was alleged to have taken bets on MLB and Nippon Professional Baseball games. (The Japan Times)
{'date': 'Jan/19/2016', 'category': 'Sports', 'event_title': False, 'event_summary': 'According to a report in The Japan Times, Major League Baseball is investigating Texas Rangers pitcher Yu Darvish as to whether he had any links with an illegal gambling ring allegedly operated by his brother Sho, who was arrested in October 2015 in Osaka on gambling charges. The ring was alleged to have taken bets on MLB and Nippon Professional Baseball games. (The Japan Times)', 'entities': ['The Japan Times', 'Major League Baseball', 'Texas Rangers (baseball)', 'Yu Darvish', 'Osaka', 'Nippon Professional Baseball'], 'person

Hi, are you there
{'date': 'Feb/01/2016', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/PKK_rebellion_(2015%E2%80%93present)'], 'event_summary': "Two Turkish Army soldiers are killed in a Kurdistan Workers' Party ambush in the southeast Diyarbakır Province. (Anadolu Post)", 'entities': ['/wiki/Turkish_Army', '/wiki/Kurdistan_Workers%27_Party', '/wiki/Diyarbak%C4%B1r_Province'], 'person': False, 'external_link': ['http://aa.com.tr/en/turkey/two-turkish-soldiers-martyred-in-pkk-attack/513442']}
{'date': 'Feb/01/2016', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/War_in_Afghanistan_(2001%E2%80%93present)'], 'event_summary': 'A Taliban suicide bomb attack outside a police office in central Kabul kills at least 9 people. (AFP via Times of India) (Sky News) (AFP via Straits Times)', 'entities': ['/wiki/Taliban', '/wiki/Suicide_bomb', '/wiki/Kabul'], 'person': False, 'external_link': ['http://timesofindia.indiatimes.com/world/south-asia/Powerful-blast-

{'date': 'Feb/18/2016', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/Ethnic_violence_in_South_Sudan'], 'event_summary': 'Fighting occurs between Shilluk and Dinka youths at a United Nations peacekeeping compound in the city of Malakal which  lasts around three hours. Médecins Sans Frontières reports  at least 18 people are  killed, including two MSF South Sudanese staff  members, and dozens wounded.  (Reuters) (Trend News Agency)', 'entities': ['/wiki/Shilluk_people', '/wiki/Dinka_people', '/wiki/United_Nations', '/wiki/Malakal', '/wiki/M%C3%A9decins_Sans_Fronti%C3%A8res'], 'person': False, 'external_link': ['https://www.reuters.com/article/us-southsudan-unrest-idUSKCN0VR1FU?feedType=RSS&feedName=worldNews', 'http://en.trend.az/world/other/2496504.html']}
{'date': 'Feb/18/2016', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/Syrian_Civil_War'], 'event_summary': 'The Syrian Army, backed by the Russian Air Force, says it has captured the town of Ki

Hi, are you there
{'date': 'Mar/01/2016', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/War_in_Donbass'], 'event_summary': 'Three soldiers are killed and two others are injured after a Ukrainian military truck was blown up in the eastern part of Luhansk Oblast.  (Ukraine Today)', 'entities': ['/wiki/Armed_Forces_of_Ukraine', '/wiki/Luhansk_Oblast'], 'person': False, 'external_link': ['http://uatoday.tv/news/military-truck-blown-up-in-luhansk-region-three-killed-two-injured-601879.html']}
{'date': 'Mar/01/2016', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/Iraqi_Civil_War_(2014%E2%80%932017)', '/wiki/American-led_intervention_in_Iraq_(2014%E2%80%93present)'], 'event_summary': "The United States Army's elite Delta Force captures their first suspected ISIL operative during a raid in northern Iraq. The detainee is being interrogated by the U.S. and is expected to be turned over to Iraqi officials in the coming days. (CNN)", 'entities': ['/wiki/Unite

...

Hi, are you there
{'date': 'Aug/01/2017', 'category': 'Armed conflicts and attacks', 'event_title': ['/wiki/War_in_Afghanistan_(2001%E2%80%93present)'], 'event_summary': 'An explosion kills at least 29 people and injures dozens more at a Shia mosque in Herat, Afghanistan. (BBC)', 'entities': ['/wiki/Herat', '/wiki/Afghanistan'], 'person': False, 'external_link': ['https://www.bbc.co.uk/news/world-asia-40797016']}
{'date': 'Aug/01/2017', 'category': 'Arts and culture', 'event_title': ['/wiki/Angkor_Wat'], 'event_summary': "A 2 meter (6.5 feet) tall 12th century sandstone statue of a human figure is unearthed by archaeologists during an excavation of a Khmer Empire-era hospital built during the reign of King Jayavarman VII at Cambodia's Angkor Wat temple complex in Siem Reap Province. (BBC)", 'entities': ['/wiki/12th_century', '/wiki/Khmer_Empire', '/wiki/Jayavarman_VII', '/wiki/Cambodia', '/wiki/Angkor_Wat', '/wiki/Siem_Reap_Province'], 'person': False, 'external_link': ['https://www.bb

{'date': 'Aug/27/2017', 'category': 'Politics and elections', 'event_title': ['/wiki/Politics_of_Guatemala'], 'event_summary': "President of Guatemala Jimmy Morales announced Sunday he is expelling the head of the International Commission against Impunity in Guatemala (CICIG), a U.N. anti-corruption commission that is investigating the president's campaign financing. (AP)\nThe Constitutional Court suspends the order made by President Jimmy Morales to expel the U.N. anti-corruption commission head. (Reuters)\nHealth Minister Lucrecia Hernández Mack and her deputies announce Sunday they have resigned. (AP)", 'entities': ['/wiki/President_of_Guatemala', '/wiki/Jimmy_Morales', '/wiki/International_Commission_against_Impunity_in_Guatemala'], 'person': False, 'external_link': ['http://hosted.ap.org/dynamic/stories/L/LT_GUATEMALA_UN_PRESIDENT', 'https://www.reuters.com/article/us-guatemala-corruption-idUSKCN1B70PT?il=0', 'http://hosted.ap.org/dynamic/stories/L/LT_GUATEMALA_UN_PRESIDENT_THE_LA

Hi, are you there
{'date': 'Sep/01/2017', 'category': 'Disasters and accidents', 'event_title': ['/wiki/2017_Atlantic_hurricane_season'], 'event_summary': 'Hurricane Irma, now a Category 2 hurricane with maximum sustained winds of 110 miles per hour (175 kilometers per hour), is expected to resume strengthening this weekend increasing the danger when it nears the Leeward Islands in the Caribbean next Thursday. (Weather Channel) (CNN) (National Hurricane Center)', 'entities': ['/wiki/2017_Atlantic_hurricane_season#Hurricane_Irma', '/wiki/Saffir%E2%80%93Simpson_scale#Category_2', '/wiki/Leeward_Islands', '/wiki/Caribbean_Sea'], 'person': False, 'external_link': ['https://weather.com/storms/hurricane/news/hurricane-irma-major-hurricane-atlantic-ocean', 'http://www.cnn.com/2017/08/31/us/hurricane-irma-forecast-weather/index.html', 'http://www.nhc.noaa.gov/text/refresh/MIATCPAT1+shtml/011449.shtml']}
{'date': 'Sep/01/2017', 'category': 'Health and medicine', 'event_title': ['/wiki/Great_Lak

{'date': 'Sep/25/2017', 'category': 'Politics and elections', 'event_title': ['/wiki/German_federal_election,_2017'], 'event_summary': 'Frauke Petry resigns as leader of the far right Alternative for Germany (AfD), a day after the party won seats in the Bundestag for the first time, saying the party has become too "anarchical" and "could not offer a credible platform". (The Guardian)', 'entities': ['/wiki/Frauke_Petry', '/wiki/Alternative_for_Germany', '/wiki/Bundestag'], 'person': False, 'external_link': ['https://www.theguardian.com/world/2017/sep/25/afd-leader-frauke-petry-quits-party-german-election-breakthrough']}
{'date': 'Sep/25/2017', 'category': 'Politics and elections', 'event_title': ['/wiki/Efforts_to_repeal_the_Patient_Protection_and_Affordable_Care_Act'], 'event_summary': 'United States Senator Susan Collins says she will vote "no" on the Graham–Cassidy bill joining Senators John McCain and Rand Paul and possibly ending the most recent effort to repeal Obamacare. (The Hil

2018 January
2018 February
2018 March
2018 April
2018 May
2018 June
2018 July
2018 August
2018 September
2018 October
2018 November
2018 December
2019 January
2019 February
2019 March
2019 April
